In [1]:
import requests
import json
import datetime as dt
import hashlib
from twisted.internet import reactor
from scrapy.crawler import CrawlerRunner
from scrapy.utils.project import get_project_settings

#from my_project.spiders.deals import DealsSpider
from bs4 import BeautifulSoup as bs

In [2]:
import urllib.request
import urllib.parse 
from urllib.request import urlopen
from urllib.request import Request
from urllib.parse import urlparse

In [3]:
def schedule_next_crawl(null, hour, minute):
    nextweek = (
        dt.datetime.now() + dt.timedelta(seconds=7)
        ).replace(hour=hour, minute=minute, second=0, microsecond=0)
    sleep_time = (nextweek - dt.datetime.now()).total_seconds()
    reactor.callLater(sleep_time, crawl)

def crawl_job():
    settings = get_project_settings()
    runner = CrawlerRunner(settings)
    return runner.crawl(DealsSpider)

def crawl():
    d = crawl_job()
    # crawl weekly at 1.30 am
    d.addCallback(schedule_next_crawl, hour=1, minute=30)

In [4]:
def get_page(url):
    response = urllib.request.urlopen(urllib.request.Request(url, 
                                                            headers={'User-Agent': 'Mozilla'} ))
    soup = bs(response, 
                         'html.parser', 
                         from_encoding=response.info().get_param('charset'))
    
    return soup

In [5]:
import pandas as pd
def roboText(robots):
    disallow = []
    lines = str(robots).splitlines()
    for line in lines:

        if line.strip():
            if not line.startswith('#'):
                split = line.split(':', maxsplit=1)
                #data.append([split[0].strip(), split[1].strip()])
                if(split[0].strip() == 'Disallow'):
                    disallow.append(split[1].strip())

    return disallow

In [6]:
robots = get_page("https://www.coventry.ac.uk/robots.txt")
roboTextDisallowList = roboText(robots)

In [7]:
def mycrawler(seed, maxcount):    
    Details = {}
    DispDescription = []
    DispList = []    
    Q = [seed]#this is the queue which initially contains the given seed URL
    count = 0
    Title = ''
    Authors = ''
    Abstract = ''
    KeyWords = ''
    Year = ''
    Month = ''
    DOI = ''
    response = requests.get(seed)
    content = bs(response.text,'html.parser')       
    Pagelinks = content.findAll('a', {'class': 'step'})
    for j in range(0, len(Pagelinks)):
        subPageLinks = Pagelinks[j]['href']
        subPageLinks = 'https://pureportal.coventry.ac.uk' + subPageLinks
        Q.append(subPageLinks)
    while(Q!=[] and count < maxcount):
        count +=1
        url = Q.pop(0)
        response = requests.get(url)
        content = bs(response.text,'html.parser')
        links = content.findAll('a', {'class': 'link'})
        for i in range(0, len(links)):
            #print(links[i],'\n')
            if(roboTextDisallowList.__contains__(links[i])):
                continue
            if not links[i]['href'].startswith('#') and not links[i]['href'].startswith('/') and '/persons/' in links[i]['href']:
                print(links[i]['href'],'\n')
                subURL = links[i]['href']
                Q.append(subURL)
                pubURL = subURL + '/publications'
                #print(pubURL)
                pubResponse = requests.get(pubURL)
                pubContent = bs(pubResponse.text,'html.parser')
                pubLinks = pubContent.findAll('a')
                for j in range(0, len(pubLinks)):
                    if not pubLinks[j]['href'].startswith('#') and not pubLinks[j]['href'].startswith('/') and '/en/publications/' in pubLinks[j]['href']:
                        #print(pubLinks[j]['href'],'\n')
                        reqURL = pubLinks[j]['href']
                        if(reqURL != None and reqURL != '/'):
                            reqURL = reqURL.strip()
                            #print(reqURL)
                            reqResponse = requests.get(reqURL)
                            reqContent = bs(reqResponse.text,'html.parser')
                            description = reqContent.find('div',{'id' : 'cite-BIBTEX'}).get_text().replace('",','/').replace(',','//').replace('booktitle','book')
                            temp = description.replace('//',',').split('/')
                            print(temp) 
                            for i in range(0, len(temp)):
                                if('title' in temp[i]):
                                    Title = temp[i].split(',')[1]
                                elif(temp[i].strip().startswith('author')):
                                    Authors = temp[i]    
                                elif(temp[i].strip().startswith('abstract')):
                                    Abstract = temp[i]
                                elif(temp[i].strip().startswith('keywords')):
                                    KeyWords = temp[i]
                                elif(temp[i].strip().startswith('year')):
                                    Year = temp[i]
                                elif(temp[i].strip().startswith('month')):
                                    Month = temp[i][0:16]
                                elif(temp[i].strip().startswith('doi')):
                                    DOI = temp[i]
                            Des = Title + Authors + Abstract + KeyWords + Year + Month + DOI
                            Details[pubLinks[j]['href']] = Des
                            #DispDetails = 'Author URL: ' + links[i]['href'] + '\n' + '   Publication URL: ' + pubLinks[j]['href'] + '  ' #+ description 
                            DispDetails = {
                                'authorUrl': subURL,
                                'publicationUrl': pubLinks[j]['href'],
                                'Description': Des
                            }
                            #print(DispDetails)
                            DispDescription.append(DispDetails)
    return(Details,DispDescription)
                        
urlDetails,DispDescription = mycrawler('https://pureportal.coventry.ac.uk/en/organisations/school-of-economics-finance-and-accounting/persons/',10)



https://pureportal.coventry.ac.uk/en/persons/mohamad-nazri-abd-karim 

['\n@article{e8161c7e698e4edcaea1ced3cf343c2b,  title     = "Stock Liquidity and SMEs{\\textquoteright} Likelihood of Bankruptcy: Evidence from the US Market', '  abstract  = "We study the association between the stock liquidity of SMEs in the US and their likelihood of bankruptcy, using a dataset that comprises information on 5075 firms over the time period from 1984 to 2013 using the hazard model of Campbell et al. (2008). We find that less liquid stocks are associated with higher probability of bankruptcy, although there is substantial heterogeneity across industries regarding the predictive power of the liquidity measure on the likelihood of bankruptcy. Furthermore, the exchange where the SMEs are listed also affects the likelihood of bankruptcy. Classification performance tests conclude that adding a liquidity measure variable to the Campbell et al. (2008) model improves its predictive power.', '  keywords  = "

['\n@conference{442b5f2f548f4da58903a455d9403a2d,  title    = "Institutional entrepreneurship in Islamic financial reporting standardisation projects', '  author   = "Ahmad Abras', '  year     = "2020', '  month    = jan,  day      = "9', '  language = "English', '  note     = "Alternative Accounts Europe 2020 Conference ; Conference date: 09-01-2020 Through 09-01-2020', '}\n']
['\n@conference{89ae7215a25540299d11a50e62c208e8,  title    = "Competing institutional logics and institutional embeddedness of actors in Islamic financial reporting standardisation: A comparative study', '  author   = "Ahmad Abras and Kelum Jayasinghe', '  year     = "2019', '  language = "English', '  note     = "British Accounting and Finance Association BAFA, BAFA ; Conference date: 08-04-2019 Through 10-04-2019', '  url      = "https:,bafa.ac.uk', 'events', 'events-past', 'bafa-annual-conference-with-doctoral-masterclasses-2019.html', '}\n']
['\n@conference{51ecd2024cad42baa3ca68b9a22882db,  title    = "Pol

['\n@article{9db1ee95e3a548029fc10a8cfa0d27ab,  title     = "The effect of government involvement and payment method on merger and acquisition performance: the case of China', '  abstract  = "This paper applies a sample of 842 to investigate the effect of government involvement and payment methods on merger and acquisition of Chinese listed firms for the period 1993 - 2015. The study employs market model as benchmark to estimate expected returns for several event windows. We find that Chinese acquirer shareholders experience higher returns from the acquisitions in firms with no government involvements than those where government is involved. Our study demonstrates that stock-financed acquisitions maximise the wealth gains of shareholders than cash-backed acquisitions. Our finding further shows that using cash to finance government backed acquisitions yields extra wealth for investors on the announcement date whilst the market experience higher abnormal returns when stocks are used to f

['\n@article{4d108bba6aae49908b8cb69e9456c436,  title     = "Understanding Public Sentiment in Relation to the African Continental Free Trade Agreement', '  abstract  = "This study explores public sentiment in relation to the African Continental Free Trade Agreement (ACFTA) by analysing 18,481 tweets mentioning ACFTA over a three-month period. The findings highlight the dominance of actors outside the African continent in the public discourse on ACFTA thus indicating the importance of the African diaspora and foreign interests in framing the debate and influencing public opinion on the continent. They also highlight the salient issues in the public debate on ACFTA to include its potential effects on national economies and jobs as well as the potential for its exploitation by foreign interests. The study also points at a disconnect between governments and politicians promoting ACFTA on the one hand and the average citizen in Africa on the other as it shows a general negative sentiment i

['\n@book{40006753aab04171a5e7d2ef0e1eefdb,  title     = "Financial Innovation and Engineering in Islamic Finance', '  abstract  = "Provides the reader with a comprehensive and original account of what constitutes a religious orientation towards financial innovation and engineering in IFIsExplains the role of religious rules in the financial innovation and engineering processes and how this role is enacted, and equips the reader with a practical framework for financial product development in IFIsExplores the historical context of financial innovation and engineering in the Islamic finance and economics thoughts over 14 centuries', '  keywords  = "Financial Engineering, Islamic Finance, Banking, Financial Innovation, Finance', '  author    = "Samir Alamad', '  note      = "Alamad, Samir. (2017). Financial Innovation and Engineering in Islamic Finance, Switzerland AG: Springer. ', '  year      = "2017', '  doi       = "10.1007', '978-3-319-52947-9', '  language  = "English', '  isbn     

...

['\n@article{bae58816471f4b7b8622ca94c545ac38,  title     = "Evaluation of merger premium and firm performance in Europe', '  abstract  = "This paper investigates whether the deal premium affects the performance of the acquiring firms in European mergers and acquisitions (M&As) deals for the period 2000-2013. We find a significant reduction in short-term performance of the acquiring firms after the M&As, reflecting the overpayment hypothesis. Our result also indicates that the negative effect on the performance of the acquiring firms is less pronounced in the long-term. The result confirms the synergy hypothesis and the existence of quadratic relationship between high premium and performance. Our findings are robust as we control for firm and time trends. The findings of our study have implications for companies engaging in acquisitions in Europe.', '  keywords  = "mergers, premiums, performance, acquisition, Europe, returns', '  author    = "Matthias Nnadi and Daniel Aghanya', '  note

['\n@article{06f0706420d04edcb54811e61419c179,  title     = "The impact of regulations on compliance costs, risk-taking, and reporting quality of the EU banks', '  abstract  = "The paper examines how the Statutory Audit and Corporate Reporting Directives (SACORD) affect the compliance costs, risk taking and quality of financial reporting of the EU banks. Using a natural experiment, we find that post SACORD, both compliance costs and risk taking increase significantly. However, the implementation of additional regulations seems to be effective in terms of improved quality of financial reporting. When we analyse the impact by size, we find that smaller banks face disproportionately higher increase in compliance costs while larger banks seem to engage in greater risk taking. ', '  keywords  = "Financial regulation, Transparency, Financial system, Financial stability, Difference-in-differences', '  author    = "Sunil Poshakwale and Daniel Aghanya and Vineet Agarwal', '  note      = "NOTICE

['\n@article{06f0706420d04edcb54811e61419c179,  title     = "The impact of regulations on compliance costs, risk-taking, and reporting quality of the EU banks', '  abstract  = "The paper examines how the Statutory Audit and Corporate Reporting Directives (SACORD) affect the compliance costs, risk taking and quality of financial reporting of the EU banks. Using a natural experiment, we find that post SACORD, both compliance costs and risk taking increase significantly. However, the implementation of additional regulations seems to be effective in terms of improved quality of financial reporting. When we analyse the impact by size, we find that smaller banks face disproportionately higher increase in compliance costs while larger banks seem to engage in greater risk taking. ', '  keywords  = "Financial regulation, Transparency, Financial system, Financial stability, Difference-in-differences', '  author    = "Sunil Poshakwale and Daniel Aghanya and Vineet Agarwal', '  note      = "NOTICE

['\n@article{06f0706420d04edcb54811e61419c179,  title     = "The impact of regulations on compliance costs, risk-taking, and reporting quality of the EU banks', '  abstract  = "The paper examines how the Statutory Audit and Corporate Reporting Directives (SACORD) affect the compliance costs, risk taking and quality of financial reporting of the EU banks. Using a natural experiment, we find that post SACORD, both compliance costs and risk taking increase significantly. However, the implementation of additional regulations seems to be effective in terms of improved quality of financial reporting. When we analyse the impact by size, we find that smaller banks face disproportionately higher increase in compliance costs while larger banks seem to engage in greater risk taking. ', '  keywords  = "Financial regulation, Transparency, Financial system, Financial stability, Difference-in-differences', '  author    = "Sunil Poshakwale and Daniel Aghanya and Vineet Agarwal', '  note      = "NOTICE

['\n@article{06f0706420d04edcb54811e61419c179,  title     = "The impact of regulations on compliance costs, risk-taking, and reporting quality of the EU banks', '  abstract  = "The paper examines how the Statutory Audit and Corporate Reporting Directives (SACORD) affect the compliance costs, risk taking and quality of financial reporting of the EU banks. Using a natural experiment, we find that post SACORD, both compliance costs and risk taking increase significantly. However, the implementation of additional regulations seems to be effective in terms of improved quality of financial reporting. When we analyse the impact by size, we find that smaller banks face disproportionately higher increase in compliance costs while larger banks seem to engage in greater risk taking. ', '  keywords  = "Financial regulation, Transparency, Financial system, Financial stability, Difference-in-differences', '  author    = "Sunil Poshakwale and Daniel Aghanya and Vineet Agarwal', '  note      = "NOTICE

In [9]:
len(urlDetails)

500

In [435]:
DispDescription[1].get('publicationUrl')

'https://pureportal.coventry.ac.uk/en/publications/personalisation-of-power-neoliberalism-and-the-production-of-corr'

In [376]:
print(DispDescription)

[{'authorUrl': 'https://pureportal.coventry.ac.uk/en/persons/mohamad-nazri-abd-karim', 'publicationUrl': 'https://pureportal.coventry.ac.uk/en/publications/stock-liquidity-and-smes-likelihood-of-bankruptcy-evidence-from-t', 'Description': '  title     = "Stock Liquidity and SMEs{\\textquoteright} Likelihood of Bankruptcy: Evidence from the US Market  author    = "{El kalak}, Izidin and Alcino Azevedo and Robert Hudson and {Abd Karim}, {Mohamad Nazri}  abstract  = "We study the association between the stock liquidity of SMEs in the US and their likelihood of bankruptcy, using a dataset that comprises information on 5075 firms over the time period from 1984 to 2013 using the hazard model of Campbell et al. (2008). We find that less liquid stocks are associated with higher probability of bankruptcy, although there is substantial heterogeneity across industries regarding the predictive power of the liquidity measure on the likelihood of bankruptcy. Furthermore, the exchange where the SMEs 

In [10]:
import re
def docClensing(docs):
    CleanedDetails = {}
    for k, v in docs.items():
        temp = re.sub(r'[^\x00-\x7F]+','',str(v))
        temp = re.sub(r'@\w+','',temp)
        temp = re.sub(r'\n','',temp)
        temp = re.sub(r'//','',temp)
        temp = re.sub(r'/','',temp)
        temp = temp.replace('{','').replace('}','').replace('=','').replace('"','').replace('\'','')
        temp = temp.replace('author','').replace('title','').replace('month','').replace('year','').replace('day','')
        temp = temp.lower()
        temp = " ".join(temp.split())
        CleanedDetails[k] = temp
    return(CleanedDetails)

CleanedDetails = docClensing(urlDetails)
CleanedDetails

{'https://pureportal.coventry.ac.uk/en/publications/stock-liquidity-and-smes-likelihood-of-bankruptcy-evidence-from-t': 'stock liquidity and smes\\textquoteright likelihood of bankruptcy: evidence from the us market el kalak, izidin and alcino azevedo and robert hudson and abd karim, mohamad nazri abstract we study the association between the stock liquidity of smes in the us and their likelihood of bankruptcy, using a dataset that comprises information on 5075 firms over the time period from 1984 to 2013 using the hazard model of campbell et al. (2008). we find that less liquid stocks are associated with higher probability of bankruptcy, although there is substantial heterogeneity across industries regarding the predictive power of the liquidity measure on the likelihood of bankruptcy. furthermore, the exchange where the smes are listed also affects the likelihood of bankruptcy. classification performance tests conclude that adding a liquidity measure variable to the campbell et al. (

In [11]:
len(CleanedDetails)

500

In [12]:
import nltk
nltk.download("stopwords")
from nltk.corpus import stopwords

sw = stopwords.words('english')
nltk.download("punkt")
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer

ps = PorterStemmer()
def stopWordStemRemoval(docs):
    StopWordStemRemoved = {}
    for k, v in docs.items():
        tokens = word_tokenize(v)
        tmp = ""
        for w in tokens:
            if w not in sw:
                tmp += ps.stem(w) + " "
        StopWordStemRemoved[k] = tmp

    return(StopWordStemRemoved)

StopWordStemRemoved = stopWordStemRemoval(CleanedDetails)
StopWordStemRemoved

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/swathipathaikara/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/swathipathaikara/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


{'https://pureportal.coventry.ac.uk/en/publications/stock-liquidity-and-smes-likelihood-of-bankruptcy-evidence-from-t': 'stock liquid smes\\textquoteright likelihood bankruptci : evid us market el kalak , izidin alcino azevedo robert hudson abd karim , mohamad nazri abstract studi associ stock liquid sme us likelihood bankruptci , use dataset compris inform 5075 firm time period 1984 2013 use hazard model campbel et al . ( 2008 ) . find less liquid stock associ higher probabl bankruptci , although substanti heterogen across industri regard predict power liquid measur likelihood bankruptci . furthermor , exchang sme list also affect likelihood bankruptci . classif perform test conclud ad liquid measur variabl campbel et al . ( 2008 ) model improv predict power . keyword market liquid , liquid measur , bankruptci , hazard model 2017 de doi 10.2139 ',
 'https://pureportal.coventry.ac.uk/en/publications/personalisation-of-power-neoliberalism-and-the-production-of-corr': 'personalis power a

In [13]:
len(StopWordStemRemoved)

500

In [138]:
if '2' in StopWordStemRemoved:
    print('Yes')

In [151]:
inverted_index = {}
def inverted_index_call(docs):
    new_terms = {}
    for k, doc in docs.items():
        new_tokens = doc.split()
        new_terms[k] = new_tokens
        for term in new_tokens:
            if term in inverted_index:
                inverted_index[term].add(k) #existing word
            else: inverted_index[term] = {k} #New word
    for term in inverted_index.keys():
        for k,doc in new_terms.items():
            if not doc.__contains__(term):
                val = list(inverted_index[term])
                if val.__contains__(k):
                    newVal = val.remove(k) #removing deleted word
                    inverted_index[term] = newVal
        
    
    return(inverted_index)
        
inverted_index = inverted_index_call(StopWordStemRemoved)
inverted_index

{'stock': {'https://pureportal.coventry.ac.uk/en/publications/a-global-analysis-of-private-investments-in-public-equity-2',
  'https://pureportal.coventry.ac.uk/en/publications/accounting-analyses-of-momentum-and-contrarian-strategies-in-emer-2',
  'https://pureportal.coventry.ac.uk/en/publications/antecedents-and-consequences-of-the-worldwide-diffusion-of-accoun',
  'https://pureportal.coventry.ac.uk/en/publications/are-domestic-firms-exposed-to-similar-currency-risk-as-internatio',
  'https://pureportal.coventry.ac.uk/en/publications/are-serial-acquirers-good-targets-for-acquisition-an-accounting-p-2',
  'https://pureportal.coventry.ac.uk/en/publications/assessing-the-effectiveness-of-internal-governance-controls-the-c',
  'https://pureportal.coventry.ac.uk/en/publications/bank-stock-valuation-theories-do-they-explain-prices-based-on-the',
  'https://pureportal.coventry.ac.uk/en/publications/ceo-compensation-option-incentives-and-information-disclosure',
  'https://pureportal.coventr

In [15]:
len(inverted_index)

6206

In [16]:
df = {}
for i in inverted_index:
    df[i] = len(inverted_index[i])

total_vocab = [x for x in df]
words_count = len(total_vocab)

import numpy as np

def tf_idf_cal(docs):
    tf_idf = {}
    N = len(docs.keys())
    for k, doc in docs.items():
        tokens = doc.split()
        #counter = i
        for token in np.unique(tokens):
            Df = df[token]
            tf = Df/words_count
            idf = np.log(N/(Df+1))
            tf_idf[k, token] = tf*idf
    return(tf_idf)

tf_idf = tf_idf_cal(StopWordStemRemoved)

words = np.array(list(inverted_index.keys()))
words

array(['stock', 'liquid', 'smes\\textquoteright', ..., '13.9', 'ringgit',
       'malaysia\\textquoteright'], dtype='<U47')

In [18]:
def vector_creation(docs):
    vector = {}
    i_tf_idf = []
    for k, doc in docs.items():
        i_tf_idf = []
        for i in range(0,len(words)):
            i_token =  words[i]
            i_vals = inverted_index[i_token]
            if(k in i_vals):
                i_tf_idf.append(tf_idf[k,i_token])
            else:
                i_tf_idf.append(0)
    
        vector[k] = np.array(i_tf_idf)
    return(vector)

vector = vector_creation(StopWordStemRemoved)
vector

{'https://pureportal.coventry.ac.uk/en/publications/stock-liquidity-and-smes-likelihood-of-bankruptcy-evidence-from-t': array([0.01997262, 0.01344161, 0.0008897 , ..., 0.        , 0.        ,
        0.        ]),
 'https://pureportal.coventry.ac.uk/en/publications/personalisation-of-power-neoliberalism-and-the-production-of-corr': array([0., 0., 0., ..., 0., 0., 0.]),
 'https://pureportal.coventry.ac.uk/en/publications/stock-price-and-volume-effects-associated-with-changes-in-the-com': array([0.01997262, 0.01344161, 0.        , ..., 0.        , 0.        ,
        0.        ]),
 'https://pureportal.coventry.ac.uk/en/publications/competing-institutional-logics-and-power-dynamics-in-islamic-fina': array([0., 0., 0., ..., 0., 0., 0.]),
 'https://pureportal.coventry.ac.uk/en/publications/the-rise-and-fall-of-institutional-entrepreneurship-in-islamic-fi': array([0., 0., 0., ..., 0., 0., 0.]),
 'https://pureportal.coventry.ac.uk/en/publications/institutional-entrepreneurship-in-islamic-fina

In [19]:
len(vector)

500

### Query Processing

In [450]:
def or_postings(posting1, posting2):
    p1 = 0
    p2 = 0
    result = list()
    posting1.sort()
    posting2.sort()
    while p1 < len(posting1) and p2 < len(posting2):
        if(posting1[p1] == posting2[p2]):
            result.append(posting1[p1])
            p1 += 1
            p2 += 1
        elif posting1[p1] > posting2[p2]:
            result.append(posting2[p2])
            p2 += 1
        else:
            result.append(posting1[p1])
            p1 += 1
    while p1 < len(posting1):
        result.append(posting1[p1])
        p1 += 1
    while p2 < len(posting2):
        result.append(posting2[p2])
        p2 += 1
    return result    
        

def and_postings(posting1,posting2):
    p1 = 0
    p2 = 0
    result = list()
    posting1.sort()
    posting2.sort()
    while p1 < len(posting1) and p2 < len(posting2):
        if(posting1[p1] == posting2[p2]):
            result.append(posting1[p1])
            p1 += 1
            p2 += 1
        elif posting1[p1] > posting2[p2]:
            p2 += 1
        else:
            p1 += 1
    return result

In [451]:
def resultedPostinglist(query):
    tokens = word_tokenize(query)
    p1 = tokens[0]
    p2 = tokens[len(tokens)-1]
    if(' or' in query or 'or ' in query):
        resultedPostingList = or_postings(list(inverted_index[p1]),list(inverted_index[p2]))
    else:
        resultedPostingList = and_postings(list(inverted_index[p1]),list(inverted_index[p2]))
        
    return(resultedPostingList)

In [452]:
def Query_TF_IDF(query):
    Qtf_idf = {}
    N = len(urlDetails)
    counter = 1
    for token in word_tokenize(query):
        Df = df[token]
        tf = Df/words_count
        idf = np.log(N/(Df+1))
        Qtf_idf[1, token] = tf*idf
    return(Qtf_idf)

In [453]:
def QvectorCreation(query):
    Qvector = {}
    Qtf_idf = Query_TF_IDF(query.replace(' and','').replace('and ','').replace(' or','').replace('or ',''))
    Qi_tf_idf = []
    for i in range(0,len(words)):
        i_token =  words[i]
        i_vals = inverted_index[i_token]
        if(i_token in word_tokenize(query)):
            Qi_tf_idf.append(Qtf_idf[1,i_token])
        else:
            Qi_tf_idf.append(0)
    
    Qvector[query] = np.array(Qi_tf_idf)
    return(Qvector)

In [454]:
import json

import math
def calc_inner(v1, v2):
    ans = 0
    for i in range(len(v1)):
        ans += v1[i]*v2[i]
    return ans

def calc_length(v):
    tmp = 0
    for x in v:
        tmp += x**2
    return tmp 

def calc_cosine(v1,v2): 
    return calc_inner(v1,v2) / (calc_length(v1)*calc_length(v2))

In [457]:
def get_similarity(query):
    similarity = {}
    DispList = []
    query = query.lower()
    resultedPostingList = resultedPostinglist(query)
    Qvector = QvectorCreation(query)
    for i in range(0,len(DispDescription)):
        for j in range(0,len(resultedPostingList)):
            if(DispDescription[i].get('publicationUrl') == resultedPostingList[j]):
                similarity[i] = calc_cosine(Qvector[query],vector[resultedPostingList[j]])
                break
            else:
                similarity[i] = 0   
    similarity_sorted = sorted(similarity.items(),key = lambda X: X[1], reverse = True)
    for k, v in similarity_sorted:
        if(v != 0.0):
            DispList.append(DispDescription[k])
    return(DispList,len(DispList))
        

In [462]:
q1 = 'eliana and 2022'
sim,doclength = get_similarity(q1)
for d in sim:
    print(d,'\n')

{'authorUrl': 'https://pureportal.coventry.ac.uk/en/persons/eliana-lauretta', 'publicationUrl': 'https://pureportal.coventry.ac.uk/en/publications/unveiling-the-black-swan-of-the-financegrowth-nexus-assumptions-a', 'Description': '  title     = "Unveiling the black swan of the finance‐growth Nexus: Assumptions and preliminary evidence of virtuous and unvirtuous cycles  author    = "Eliana Lauretta and Chaudhry, {Sajid M.} and Daniel Santamaria  abstract  = "Empirical evidence behind the nature of the finance-growth nexus and mediating drivers behind this association is well documented in the literature. However, a framework that depicts the association between credit creation, financial innovation and endogenous creation of boom-bust cycles is less evident and the gap between empirical research and theoretical development remains. Hence, this study represents a first attempt to provide a framework that could explain the switch of economic cycles from virtuous to unvirtuous and vice ver

In [463]:
print(doclength)

2
